In [1]:
import pandas as pd
import numpy as np
import time
import os

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import LabelEncoder

from data_reduction.ranking import getPHOutlierScores_restrictedDim as phl_selection
from data_reduction.representativeness import find_epsilon

import seaborn as sns
import matplotlib.pyplot as plt

import sys
sys.path.append('../')
from my_dataset_reduction.phl import getPHOutlierScores_restrictedDim as my_phl_selection, estimate_delta

dbpath = '../datasets/dry+bean+dataset/DryBeanDataset/Dry_Bean_Dataset.xlsx'
target = 'Class'

SEED = 2025
np.random.seed(SEED)

PROFILING = False # False para tomar todo el dataset
results_folder = '../results/compare'

# Check if the results folder exists, if not create it
if not os.path.exists(results_folder):
    os.makedirs(results_folder)

TOL = 1e-2 # Tolerancia para ver si los scores son iguales

In [2]:
df = pd.read_excel(dbpath, )

pd.set_option('display.max_columns', None)
print("Tamaño del dataset: ", df.shape)
df.describe()

Tamaño del dataset:  (13611, 17)


Area     Perimeter  MajorAxisLength  MinorAxisLength  \
count   13611.000000  13611.000000     13611.000000     13611.000000   
mean    53048.284549    855.283459       320.141867       202.270714   
std     29324.095717    214.289696        85.694186        44.970091   
min     20420.000000    524.736000       183.601165       122.512653   
25%     36328.000000    703.523500       253.303633       175.848170   
50%     44652.000000    794.941000       296.883367       192.431733   
75%     61332.000000    977.213000       376.495012       217.031741   
max    254616.000000   1985.370000       738.860153       460.198497   

       AspectRation  Eccentricity     ConvexArea  EquivDiameter        Extent  \
count  13611.000000  13611.000000   13611.000000   13611.000000  13611.000000   
mean       1.583242      0.750895   53768.200206     253.064220      0.749733   
std        0.246678      0.092002   29774.915817      59.177120      0.049086   
min        1.024868      0.218951   20684.000000     161.243764      0.555315   
25%        1.432307      0.715928   36714.500000     215.068003      0.718634   
50%        1.551124      0.764441   45178.000000     238.438026      0.759859   
75%        1.707109      0.810466   62294.000000     279.446467      0.786851   
max        2.430306      0.911423  263261.000000     569.374358      0.866195   

           Solidity     roundness   Compactness  ShapeFactor1  ShapeFactor2  \
count  13611.000000  13611.000000  13611.000000  13611.000000  13611.000000   
mean       0.987143      0.873282      0.799864      0.006564      0.001716   
std        0.004660      0.059520      0.061713      0.001128      0.000596   
min        0.919246      0.489618      0.640577      0.002778      0.000564   
25%        0.985670      0.832096      0.762469      0.005900      0.001154   
50%        0.988283      0.883157      0.801277      0.006645      0.001694   
75%        0.990013      0.916869      0.834270      0.007271      0.002170   
max        0.994677      0.990685      0.987303      0.010451      0.003665   

       ShapeFactor3  ShapeFactor4  
count  13611.000000  13611.000000  
mean       0.643590      0.995063  
std        0.098996      0.004366  
min        0.410339      0.947687  
25%        0.581359      0.993703  
50%        0.642044      0.996386  
75%        0.696006      0.997883  
max        0.974767      0.999733

In [3]:
if PROFILING:
    df = df.sample(1000, random_state=SEED)

In [4]:
# Train test split
X = df.drop(columns=[target])
X = np.array(X)

# Convertir la columna target a entero
if not pd.api.types.is_integer_dtype(df[target]):
    le = LabelEncoder()
    y = le.fit_transform(df[target])
else:
    y = df[target].values

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=2025)

In [5]:
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)

In [6]:
reduction_methods = ['PHL', 'MY_PHL']
reps = 1 #2
deltas = [0.05, 0.1, 0.25]
metrics = ['time']

df_compare_phl = pd.DataFrame(columns=['delta', 'k'] + ['time_' + m for m in reduction_methods])

if os.path.exists(results_folder + '/compare_phl.csv'):
    df_compare_phl = pd.read_csv(results_folder + '/compare_phl.csv')
else:
    for delta in deltas:
        for n in range(reps):
            print(f"Reducing dataset delta: {delta}, iteration: {n}")
            # Reduce the dataset using PHL method
            t0 = time.time()
            outlier_scores_point_cloud_original_order,set_of_super_outliers, super_outlier_indices = phl_selection(X_train_scaled, delta, 1)
            reduction_time = time.time() - t0
            print(f"PHL: {reduction_time:.2f} seconds")

            # Reduce the dataset using my PHL method
            t0 = time.time()
            my_outlier_scores_point_cloud_original_order,my_set_of_super_outliers, my_super_outlier_indices = my_phl_selection(X_train_scaled, delta, 1)
            reduction_time_my = time.time() - t0

            print(f"MY_PHL: {reduction_time_my:.2f} s")

            # Store the results
            df_compare_phl = df_compare_phl.append({
                        'delta': delta,
                        'k': 'N/A',
                        'time_PHL' : reduction_time,
                        'time_MY_PHL' : reduction_time_my,
                        'equal' : np.allclose(outlier_scores_point_cloud_original_order, my_outlier_scores_point_cloud_original_order, atol=TOL),
                    }, ignore_index=True)
    # Save the results
    df_compare_phl.to_csv(f'{results_folder}/phl_results.csv', index=False)

Reducing dataset delta: 0.05, iteration: 0
PHL: 45.13 seconds
MY_PHL: 3.38 s
Reducing dataset delta: 0.1, iteration: 0


/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(


PHL: 44.40 seconds
MY_PHL: 3.59 s
Reducing dataset delta: 0.25, iteration: 0


/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  

PHL: 49.31 seconds
MY_PHL: 3.51 s


In [7]:
df_compare_phl

delta    k   time_PHL  time_MY_PHL  equal
0   0.05  N/A  45.134065     3.383954    1.0
1   0.10  N/A  44.401872     3.588667    1.0
2   0.25  N/A  49.310408     3.510012    1.0

In [8]:
k_values = [2, 3, 5, 7, 10]
for k in k_values:
            print(f"Reducing dataset k: {k}, iteration: {n}")
            # Estimate delta for the given k
            t0 = time.time()
            delta = estimate_delta(X_train_scaled, y_train, k)
            delta_time = time.time() - t0
            # Reduce the dataset using PHL method
            t0 = time.time()
            outlier_scores_point_cloud_original_order,set_of_super_outliers, super_outlier_indices = phl_selection(X_train_scaled, delta, 1)
            reduction_time = time.time() - t0
            print(f"PHL: {reduction_time:.2f} seconds")

            # Reduce the dataset using my PHL method
            t0 = time.time()
            my_outlier_scores_point_cloud_original_order,my_set_of_super_outliers, my_super_outlier_indices = my_phl_selection(X_train_scaled, delta, 1)
            reduction_time_my = time.time() - t0

            print(f"MY_PHL: {reduction_time_my:.2f} s")

            # Store the results
            df_compare_phl = df_compare_phl.append({
                        'delta': delta,
                        'k': k,
                        'time_PHL' : reduction_time,
                        'time_MY_PHL' : reduction_time_my,
                        'equal' : np.allclose(outlier_scores_point_cloud_original_order, my_outlier_scores_point_cloud_original_order, atol=TOL),
                    }, ignore_index=True)

Reducing dataset k: 2, iteration: 0


/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  

PHL: 50.42 seconds
MY_PHL: 4.42 s
Reducing dataset k: 3, iteration: 0


/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:247: UserWarning: The input matrix is square, but the distance_matrix flag is off.  Did you mean 

PHL: 52.39 seconds
MY_PHL: 5.14 s
Reducing dataset k: 5, iteration: 0


...

PHL: 60.81 seconds
MY_PHL: 7.70 s
Reducing dataset k: 7, iteration: 0


/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  

PHL: 72.50 seconds
MY_PHL: 10.78 s
Reducing dataset k: 10, iteration: 0


/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  warnings.warn(
/home/santiago/miniconda3/envs/data_reduction/lib/python3.9/site-packages/ripser/ripser.py:253: UserWarning: The input point cloud has more columns than rows; did you mean to transpose?
  

PHL: 92.45 seconds
MY_PHL: 16.71 s


In [9]:
df_compare_phl

delta    k   time_PHL  time_MY_PHL  equal
0  0.050000  N/A  45.134065     3.383954    1.0
1  0.100000  N/A  44.401872     3.588667    1.0
2  0.250000  N/A  49.310408     3.510012    1.0
3  0.479215    2  50.421326     4.423294    1.0
4  0.524332    3  52.393762     5.140969    1.0
5  0.585827    5  60.807412     7.697428    1.0
6  0.627999    7  72.496168    10.777594    1.0
7  0.675300   10  92.446287    16.714988    1.0